In [23]:
import re
from typing import Union

import aiohttp
from bs4 import BeautifulSoup
from pydantic import BaseModel
from tqdm.asyncio import tqdm
from tenacity import retry, stop_after_attempt, wait_exponential

# from wikiquote_tv.constants import idxurls, timeout, wikiquote_url
wikiquote_url = "https://en.wikiquote.org"

a_through_h = f"{wikiquote_url}/wiki/List_of_television_shows_(A%E2%80%93H)"
i_through_p = f"{wikiquote_url}/wiki/List_of_television_shows_(I%E2%80%93P)"
q_through_z = f"{wikiquote_url}/wiki/List_of_television_shows_(Q%E2%80%93Z)"

idxurls = [
    a_through_h,
    i_through_p,
    q_through_z,
]

timeout = 10


class Action(BaseModel):
    text: str

    def __str__(self):
        return self.text


class Quote(BaseModel):
    speaker: str
    text: str

    def __str__(self):
        return f"{self.speaker}: {self.text}"


class Conversation(BaseModel):
    quotes: list[Union[Quote, Action]]

    def __str__(self):
        return "\n".join(str(quote) for quote in self.quotes)

    def format_example(self) -> dict:
        input_text = (
            "\n".join(str(quote) for quote in self.quotes[:-1])
            + "\n"
            + self.quotes[-1].speaker
            + ": "
        )
        target_text = self.quotes[-1].text
        return {"input_text": input_text, "target_text": target_text}


def parse_quote(quote):
    try:
        speaker = quote.find("b").text
    except AttributeError:
        return Action(text=quote.text)
    text = quote.text.replace(speaker, "").strip(": ")
    return Quote(text=text, speaker=speaker)


@retry(stop=stop_after_attempt(3), wait=wait_exponential(multiplier=1, min=4, max=10))
async def get_shows(session: aiohttp.ClientSession) -> dict[str, str]:
    def get_links(soup) -> dict[str, str]:
        def _gen():
            h2_tags = soup.find_all("h2")

            start = h2_tags[0]  # includes existing and requested
            end = h2_tags[2]  # Notes

            existing = ""
            for elem in start.next_siblings:
                if elem == end:
                    break
                existing += str(elem)
            new_soup = BeautifulSoup(existing, "html.parser")
            for link in new_soup.find_all("li"):
                if link.a:
                    relative_path = link.a["href"].strip("/")
                    link_url = f"{wikiquote_url}/{relative_path}"
                    try:
                        name = link.a["title"]
                    except KeyError:
                        continue
                    if name.endswith("(page does not exist)"):
                        continue
                    yield name, link_url

        return dict(_gen())

    result = {}
    async for url in tqdm(idxurls):
        resp = await session.get(url, timeout=timeout)
        content = await resp.text()
        soup = BeautifulSoup(content)
        links = get_links(soup)
        result.update(links)
    return result


def season_links(soup: BeautifulSoup) -> Union[set, None]:
    pattern = re.compile(r"\(season_\d+\)$")
    return {
        f"{wikiquote_url}/{a['href'].strip('/')}"
        for a in soup.find_all("a", href=lambda x: x and pattern.search(x))
    } or None


def show_season(soup: BeautifulSoup) -> dict[str, str]:
    show_season_pat = re.compile(r"^(?P<show>.*?)(?: \(season (?P<season>\d+)\))?$")
    show_season_text = soup.find("h1").text
    show_season_match = show_season_pat.match(show_season_text)
    if show_season_match is None:
        raise ValueError(
            f"Could not parse show and season from {show_season_text}",
        )
    return show_season_match.groupdict()


def episode_objects(soup: BeautifulSoup) -> list[tuple[str, str, Conversation]]:
    # Assuming `soup` is your BeautifulSoup object
    contents = soup.find_all(["h3", "dl", "p", "hr"])  # Include 'h3' in the search

    merged_dls = []
    temp_content = ""
    inside_dl = False
    current_title = None
    next_title = None

    show_name = show_season(soup)["show"]

    for content in contents:
        if content.name == "h3":
            # If inside a <dl>, close it before starting a new section
            if inside_dl:
                merged_dls.append((current_title, temp_content))
                temp_content = ""
                inside_dl = False

            # Store the next title
            next_title = content.get_text()

        elif content.name == "dl":
            if not inside_dl:
                # Start of a new <dl> section, update the current title
                current_title = next_title
                temp_content = str(content)
                inside_dl = True
            else:
                # Continue the current <dl> section
                temp_content += str(content)

        elif content.name == "p" and inside_dl:
            # Part of a split <dl> section
            temp_content += str(content)

        elif content.name == "hr":
            # <hr> tag encountered, end current <dl> if within one
            if inside_dl:
                merged_dls.append((current_title, temp_content))
                temp_content = ""
                inside_dl = False

    # Add the last <dl> section if the loop ends while inside a <dl>
    if inside_dl:
        merged_dls.append((current_title, temp_content))

    editpat = re.compile(r"\[edit]$")

    def _gen():
        for title, dl in merged_dls:
            if isinstance(title, str):
                title = editpat.sub("", title)
                dlsoup = BeautifulSoup(dl, "html.parser")
                conversation = Conversation(
                    quotes=[parse_quote(quote) for quote in dlsoup.find_all("dd")],
                )
                yield show_name, title, conversation

    return list(_gen())


@retry(stop=stop_after_attempt(3), wait=wait_exponential(multiplier=1, min=4, max=10))
async def longurllist(test: bool = False) -> list[tuple[str, str, Conversation]]:
    async with aiohttp.ClientSession() as session:

        async def _gen():
            shows = await get_shows(session)
            show_items = shows.items() if not test else list(shows.items())[:3]
            async for show, url in tqdm(show_items):
                show_resp = await session.get(url, timeout=timeout)
                show_text = await show_resp.text()
                show_soup = BeautifulSoup(show_text)
                show_season_links = season_links(show_soup)
                if show_season_links is None:
                    for ep_obj in episode_objects(show_soup):
                        yield ep_obj

                else:
                    async for season_url in tqdm(show_season_links):
                        season_resp = await session.get(season_url, timeout=timeout)
                        season_text = await season_resp.text()
                        season_soup = BeautifulSoup(season_text)
                        for ep_obj in episode_objects(season_soup):
                            yield ep_obj

        return [ep_obj async for ep_obj in _gen()]


In [8]:
import asyncio
import nest_asyncio

nest_asyncio.apply()

In [24]:
%%time

results = asyncio.run(longurllist(test=False))

100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:00<00:00, 10.79it/s]

100%|██████████████████████████████████████████████████████████████████████████████| 1147/1147 [06:16<00:00,  3.04it/s]

Wall time: 6min 17s


In [26]:
import pandas as pd

df = pd.DataFrame(results, columns=['show', 'episode', 'conversation'])

In [32]:
df.head()

show       episode  \
0  10 Things I Hate About You (TV series)  Pilot [1.01]   
1  10 Things I Hate About You (TV series)  Pilot [1.01]   
2  10 Things I Hate About You (TV series)  Pilot [1.01]   
3  10 Things I Hate About You (TV series)  Pilot [1.01]   
4  10 Things I Hate About You (TV series)  Pilot [1.01]   

                                        conversation  
0  Bianca: How do I look?\nKat: Shallow.\nBianca:...  
1  Kat: What do you want?\nPatrick: What you mean...  
2  Bianca: [to Kat] You've ruined my chances of b...  
3  Kat: [to Patrick] Why are people scared of you...  
4  Chastity: My neck is sore.\nKat: That's probab...

In [33]:
df['conversation'][0]

Conversation(quotes=[Quote(speaker='Bianca', text='How do I look?'), Quote(speaker='Kat', text='Shallow.'), Quote(speaker='Bianca', text='(happy) Thank you!')])

In [93]:
import unicodedata

def format_example_2(convo: Conversation) -> dict:
    input_text = "\n".join(str(quote) for quote in convo.quotes[:-1])
    try:
        target_text = convo.quotes[-1].text
    except IndexError:
        print(convo)
        return None
    try:
        return {
            k: unicodedata.normalize('NFKD', v).encode('ASCII', 'ignore').decode()
            for k, v in {"input_text": input_text, "speaker": convo.quotes[-1].speaker, "target_text": target_text}.items()
        }
    except AttributeError:
        return None

In [94]:
%%time

df = df.assign(turns=df['conversation'].apply(lambda c: len(c.quotes)))

Wall time: 128 ms


In [95]:
df['tgtdict'] = df['conversation'].apply(format_example_2)

In [96]:
train_df = df.dropna(subset=['tgtdict'])

In [97]:
len(df), len(train_df)

(145354, 139823)

In [98]:
%%time

train_df = train_df.join(train_df['tgtdict'].apply(pd.Series))

Wall time: 23.2 s


In [99]:
train_df.head()

show       episode  \
0  10 Things I Hate About You (TV series)  Pilot [1.01]   
1  10 Things I Hate About You (TV series)  Pilot [1.01]   
2  10 Things I Hate About You (TV series)  Pilot [1.01]   
3  10 Things I Hate About You (TV series)  Pilot [1.01]   
4  10 Things I Hate About You (TV series)  Pilot [1.01]   

                                        conversation  \
0  Bianca: How do I look?\nKat: Shallow.\nBianca:...   
1  Kat: What do you want?\nPatrick: What you mean...   
2  Bianca: [to Kat] You've ruined my chances of b...   
3  Kat: [to Patrick] Why are people scared of you...   
4  Chastity: My neck is sore.\nKat: That's probab...   

                                             tgtdict  turns  \
0  {'input_text': 'Bianca: How do I look?
Kat: Sh...      3   
1  {'input_text': 'Kat: What do you want?
Patrick...      6   
2  {'input_text': 'Bianca: [to Kat] You've ruined...      4   
3  {'input_text': 'Kat: [to Patrick] Why are peop...      4   
4  {'input_text': 'Chastity: My neck is sore.
Kat...      5   

                                          input_text         speaker  \
0              Bianca: How do I look?\nKat: Shallow.          Bianca   
1  Kat: What do you want?\nPatrick: What you mean...         Patrick   
2  Bianca: [to Kat] You've ruined my chances of b...             Kat   
3  Kat: [to Patrick] Why are people scared of you...         Patrick   
4  Chastity: My neck is sore.\nKat: That's probab...  Kat and Bianca   

                                         target_text  
0                                 (happy) Thank you!  
1  [smiling] : Sure they are. That's why I find y...  
2          Kim Jong II, the dictator of North Korea!  
3  Sure they are. That's why I find you interesting.  
4                                               Dad!

In [100]:
len(train_df)

139823

In [101]:
train_df_dropna = train_df.drop(columns=['conversation', 'tgtdict']).dropna(axis=0, how='any').dropna(axis=1, how='any')

In [102]:
len(train_df_dropna)

139823

In [103]:
train_df_dropna.head()

show       episode  turns  \
0  10 Things I Hate About You (TV series)  Pilot [1.01]      3   
1  10 Things I Hate About You (TV series)  Pilot [1.01]      6   
2  10 Things I Hate About You (TV series)  Pilot [1.01]      4   
3  10 Things I Hate About You (TV series)  Pilot [1.01]      4   
4  10 Things I Hate About You (TV series)  Pilot [1.01]      5   

                                          input_text         speaker  \
0              Bianca: How do I look?\nKat: Shallow.          Bianca   
1  Kat: What do you want?\nPatrick: What you mean...         Patrick   
2  Bianca: [to Kat] You've ruined my chances of b...             Kat   
3  Kat: [to Patrick] Why are people scared of you...         Patrick   
4  Chastity: My neck is sore.\nKat: That's probab...  Kat and Bianca   

                                         target_text  
0                                 (happy) Thank you!  
1  [smiling] : Sure they are. That's why I find y...  
2          Kim Jong II, the dictator of North Korea!  
3  Sure they are. That's why I find you interesting.  
4                                               Dad!

In [104]:
str(train_df_dropna.iloc[1]['target_text'])

"[smiling] : Sure they are. That's why I find you interesting [he goes away in his motorcycle]"

In [111]:
more_than_one_turn = train_df_dropna.loc[train_df_dropna['turns'] > 1]

In [114]:
more_than_one_turn.to_parquet("wikiquote_tv.parquet", index=False)